# Unweighted Average

In [1]:
# Importing the libraries
import numpy as np
import pandas as pd
import sklearn
import matplotlib.pyplot as plt
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)

# Importing the dataset
dataset = pd.read_csv('CVD dataset2.csv')
data=dataset.iloc[:, :].values
X = dataset.iloc[:, :-1].values
y = dataset.iloc[:, 16].values
# X = dataset.iloc[:, [ 0, 1, 2, 5, 10, 11, 13, 15]].values

rows = len(data)    # 3 rows in your example
cols = len(data[0])
print(rows)
print(cols)

560
17


In [2]:
dataNoCvd = data[~(data[:,16] > 0.0)]
dataCvd = data[~(data[:,16] < 1.0)]
rowsNoCvd = len(dataNoCvd)    
rowsCvd = len(dataCvd)
print(rowsNoCvd)
print(rowsCvd)
# print(dataNoCvd)
# print(dataCvd)

519
41


In [3]:
def find_NoCvd_limitsArray(i,DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue):
    if i>0 :
        DownNoCvd = UpNoCvd
        UpNoCvd= fold_NoCvd_total+UpNoCvd
    if i < fold_NoCvd_residue :
        UpNoCvd+= 1
#     print("NoCvd limits, Down :",DownNoCvd,"Up ",UpNoCvd)
    return   DownNoCvd, UpNoCvd   
 
def find_Cvd_limitsArray(i,DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv):
    if i>0 :
        DownCvd = UpCvd
        UpCvd= fold_Cvd_total+UpCvd
    if i >= cv - fold_Cvd_residue :
         UpCvd+= 1     
#     print("Cvd limits, Down :",DownCvd,"Up ",UpCvd)
    return   DownCvd, UpCvd  

def find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1=dataNoCvd[DownNoCvd:UpNoCvd,:]
    temp2=dataCvd[DownCvd:UpCvd,:]
    temp3=np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

def find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1 = np.delete(dataNoCvd, slice(DownNoCvd, UpNoCvd), axis=0)
    temp2 = np.delete(dataCvd, slice(DownCvd, UpCvd), axis=0)
    temp3 = np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

In [4]:
def create_train_test_sets(cv,dataNoCvd,dataCvd):
    test_total = []
    train_total = []
    train_total_Cvd = []
    train_total_NoCvd = []
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)

    fold_Cvd_total = rowsCvd//cv
    fold_Cvd_residue= rowsCvd%cv
    print("fold_Cvd_total  :",fold_Cvd_total," fold_Cvd_residue  :",fold_Cvd_residue)

    fold_NoCvd_total = rowsNoCvd//cv
    fold_NoCvd_residue= rowsNoCvd%cv
    print("fold_NoCvd_total:",fold_NoCvd_total,"fold_NoCvd_residue:",fold_NoCvd_residue)

    DownNoCvd=0
    DownCvd=0
    UpNoCvd = fold_NoCvd_total
    UpCvd = fold_Cvd_total

    for i in range(cv):
        X_test = []
        y_test = []
        X_train = []
        y_train = []
#         print("============",i,"==============")
        DownNoCvd, UpNoCvd = find_NoCvd_limitsArray(i, DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue)
        DownCvd, UpCvd = find_Cvd_limitsArray(i, DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv)

        testSubset_NoCvd ,testSubset_Cvd ,testSubset_total = find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
        trainSubset_NoCvd ,trainSubset_Cvd ,trainSubset_total = find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
     
    #creating X_train, y_train, X_test, y_test
        X_test.append(np.delete(testSubset_total, 16, axis=1))
        y_test_temp = np.delete(testSubset_total, slice(0, 16), axis=1)
        y_test.append(np.reshape(y_test_temp, len(y_test_temp)))
        X_test_temp = np.array(X_test)
        X_test = X_test_temp[0]
        y_test_temp = np.array(y_test)
        y_test = y_test_temp[0]
    
        X_train.append(np.delete(trainSubset_total, 16, axis=1))
        y_train_temp = np.delete(trainSubset_total, slice(0, 16), axis=1)
        y_train.append(np.reshape(y_train_temp, len(y_train_temp)))
        X_train_temp = np.array(X_train)
        X_train = X_train_temp[0]
        y_train_temp = np.array(y_train)
        y_train = y_train_temp[0]
        
    #add every subset in a list so we can handle thm later 
        test_total.append([X_test,y_test])
        train_total.append([X_train,y_train]) 
        train_total_NoCvd.append(trainSubset_NoCvd)
        train_total_Cvd.append(trainSubset_Cvd)
    return train_total, test_total, train_total_NoCvd, train_total_Cvd

In [5]:
train_total, test_total, train_total_NoCvd, train_total_Cvd = create_train_test_sets(10,dataNoCvd,dataCvd)

fold_Cvd_total  : 4  fold_Cvd_residue  : 1
fold_NoCvd_total: 51 fold_NoCvd_residue: 9


In [6]:
# Chech ratio in each train and test set
def find_ratio(index_list):
    one = 0
    lenght=len(index_list[0])
    for i in range(lenght):
#         print(index_list[1])
        if index_list[1][i] == 1.0 :
            one+= 1
    ratio = one/lenght
    return ratio

for i in range(10):
    print(len(train_total[i][0]))
    ratio = find_ratio(train_total[i])
    print("ratio in train set:", ratio)
    ratio = find_ratio(test_total[i])
    print("ratio in test set:", ratio)

504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07142857142857142
ratio in test set: 0.08928571428571429


In [7]:
from xgboost import XGBClassifier


def my_fit(ratio,dataNoCvd,dataCvd,params):   
    Subarray=[]
    models = []
    # yarray
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)
#     print("Size of NoCvd cases in train set:",rowsNoCvd)
#     print("Size of Cvd cases in train set  :",rowsCvd)


    numOfSubsamples = rowsNoCvd//(rowsCvd*ratio)
    numOfSubsamples= int(numOfSubsamples)
    SubNoCvd = rowsNoCvd//numOfSubsamples
    residue = rowsNoCvd- SubNoCvd*numOfSubsamples


    Up = 0


    for i in range(numOfSubsamples):
        
        classifier = XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=params[5],
                  colsample_bynode=1, colsample_bytree=1, gamma=params[4],
                  learning_rate=params[0], max_delta_step=0, max_depth=params[1],
                  min_child_weight=params[3], missing=None, n_estimators=params[2], n_jobs=1,
                  nthread=None, objective='binary:logistic', random_state=0,
                  reg_alpha=0, reg_lambda=params[6], scale_pos_weight=params[7], seed=None,
                  silent=None, subsample=1.0, verbosity=1)
    #     print(i)
    #Creating the training set for each model
        Down = Up
        Up= Up + SubNoCvd
        if i < residue :
            Up+= 1
        
#         print(Down)
#         print(Up)
        
        Sub1=dataNoCvd[Down:Up,:]
        Sub2=np.concatenate((Sub1, dataCvd))
        Subarray.append(Sub2)
        
    #Dividing to X and y of the previous traing set    
        X=np.delete(Subarray[i], 16, axis=1)
        y=np.delete(Subarray[i], slice(0, 16), axis=1)
        y=np.reshape(y, len(y))
        
        classifier.fit( X, y)
        models.append(classifier)
    return models     

In [39]:
models = my_fit(2,dataNoCvd,dataCvd)   

TypeError: my_fit() missing 1 required positional argument: 'params'

In [8]:


def predict_unweighted_average(models,X):
    y_pred = []
    y_pred_models = []

    models_size = len(models)
    X_size = len(X)
       
    #βρίσκω και αποθηκευω τα predictions κάθε μοντέλου για το Χ_test όχι όμως με την μορφή (0,1) όπως θα έκανε η
# predict αλλά με μορφή πιθανότητας να έρθει 1 με την predict_proba, δηλαδή τώρα ο πίνακας y_pred_models έχει τις 
# πιθανότητες κάθε περίπτωση του X_test να εμφανίσει Cvd
    for i in range(models_size): 
        y_pred_models.append(models[i].predict_proba(X)[:,1]) 

#Παίρνω τις πιθανότητες κάθε μοντέλου και για κάθε μία περίπτωση του X_test κάνω το average των πιθανοτήτων αυτών
# οπότε βγαίνει μια μέση πιθανότητα για κάθε μία περίπτωση του X_test.
    for j in range(X_size):
        sum = 0
        for i in range(models_size):
            sum = sum + y_pred_models[i][j]
        avr = sum/models_size
        if avr>= 0.5 :         #Όμως επειδή θεωρώ ότι το μοντέλο κάνει classification αν η μέση πιθανότητα 
            y_pred.append(1.)  # είναι μεγαλυτερη από 0.5 τότε θα επιστρέφει 1, δηλαδή ότι έχει cvd, αλλιώς 0
        else:
            y_pred.append(0.)
    return y_pred        
  

In [24]:
y_pred = predict_unweighted_average(models,test_total[9][0])

In [25]:
print(y_pred)
# print(y_pred_models[0])

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 1.0]


In [9]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from sklearn import metrics

def my_cross_val( cv, train_total, test_total, train_total_NoCvd, train_total_Cvd,params):
    accuracy = []
    specificity = []
    sensitivity = []
    auc = []
    
    # print(X)
    for i in range(cv):
#         X_train = train_total[i][0]
#         y_train = train_total[i][1]
        X_test = test_total[i][0]
        y_test = test_total[i][1]
        


        models = my_fit( 3, train_total_NoCvd[i], train_total_Cvd[i],params)


        y_pred = predict_unweighted_average(models,X_test)

        cm = confusion_matrix(y_test, y_pred)
    #     print(cm)

        total1=sum(sum(cm))
        #####from confusion matrix calculate accuracy
        accuracy1=(cm[0,0]+cm[1,1])/total1
    #   print ('Accuracy : ', accuracy1)

        specificity1 = cm[0,0]/(cm[0,0]+cm[0,1])
    #   print('Specificity : ', specificity1 )

        sensitivity1 = cm[1,1]/(cm[1,0]+cm[1,1])
    #   print('Sensitivity : ', sensitivity1)
        
#         y = np.array(y_test)
#         pred = np.array(y_pred)
#         fpr, tpr, thresholds = metrics.roc_curve(y, pred, pos_label=2)
#         auc1 = metrics.auc(fpr, tpr)
        
        auc1 = roc_auc_score(y_test, y_pred)

    
        accuracy.append(accuracy1)
        specificity.append(specificity1)
        sensitivity.append(sensitivity1) 
        auc.append(auc1)
    return accuracy, specificity, sensitivity, auc

In [28]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/        
params = {
                    "learning_rate"    :[ 0.1, 0.2, 0.3],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300],
                     "subsample"       :[0.5,0.75, 1.0],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3]
        }
parameters : [0.5, 1, 100, 1, 0, 1.0, 1, 5]
accuracy : 0.6125
spes     : 0.6110105580693816
sens     : 0.64
auc      : 0.6255052790346908



In [23]:
params = {
                    "learning_rate"    :[ 0.5],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100],
                    "min_child_weight" :[1],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[1.0], #0.5-1
                     "reg_lambda"      :[1], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[5]
        }

In [24]:
comb = compute_comb(params)
print(comb[0])
accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,comb[0])

[0.5, 1, 100, 1, 0, 1.0, 1, 5]


In [25]:
from statistics import mean
print(mean(accuracy))
print(mean(specificity))
print(mean(sensitivity))
print(mean(auc))

0.6267857142857143
0.6262820512820513
0.64
0.6331410256410256


In [10]:
# https://www.geeksforgeeks.org/python-all-possible-permutations-of-n-lists/

def compute_comb(params):
    
    # initializing lists 
    list1 = params.get("learning_rate")
    list2 = params.get("max_depth")
    list3 = params.get("n_estimators") 
    list4 = params.get("min_child_weight")
    list5 = params.get("gamma")    
    list6 = params.get("colsample_bytree")
    list7 = params.get("reg_lambda") 
    list8 = params.get("scale_pos_weight")

#     # printing lists  
#     print ("The original lists are : " + str(list1) +
#                                    " " + str(list2) + 
#                                    " " + str(list3) + 
#                                    " " + str(list4) + 
#                                    " " + str(list5) + 
#                                    " " + str(list6) +
#                                    " " + str(list7) +
#                                    " " + str(list8)) 

    # using list comprehension  
    # to compute all possible permutations 
    res = [[i, j, k, l, m, n, o, p] for i in list1  
                                    for j in list2 
                                    for k in list3 
                                    for l in list4 
                                    for m in list5 
                                    for n in list6 
                                    for o in list7
                                    for p in list8] 

    # printing result 
#     print ("All possible permutations are : " +  str(res))
    return res

In [11]:
class style:
    BOLD = '\033[1m'
    END = '\033[0m'

In [12]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from statistics import mean

def gridsearch(params):
    max_sens = 0
    max_spes = 0
    max_acc = 0
    best_params = []
    max_params = []
    max_auc = 0
    combs = compute_comb(params)
    print(len(combs))
    for j in range(len(combs)):
        print(j)
        accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,combs[j])
        if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
            print(combs[j])
            print (style.BOLD + 'accuracy    ' + style.END, mean(accuracy))
            print (style.BOLD + 'specificity ' + style.END, mean(specificity))
            print (style.BOLD + 'sensitivity ' + style.END, mean(sensitivity))
            print (style.BOLD + 'auc         ' + style.END, mean(auc))
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
        else:
            print(combs[j])
            print("accuracy    ",mean(accuracy))
            print("specificity ",mean(specificity))
            print("sensitivity ",mean(sensitivity))
            print("auc         ",mean(auc))
        best_params.append([combs[j],mean(accuracy),mean(specificity),mean(sensitivity),mean(auc)])
        if mean(auc)> max_auc:
            max_sens = mean(sensitivity)
            max_spes = mean(specificity)
            max_acc = mean(accuracy)
            max_auc = mean(auc)
            max_params = combs[j]
    return max_sens, max_params, max_spes, max_acc, max_auc, best_params

# Ratio = 2

 Αποτέλεσμα της gridsearch με τις ακόλουθες παραμέτρους, γίνονται print όλα και αυτά που ικανοποιούν την συνθήκη : if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5 είναι με bold και μεταξύ γραμμών.

In [13]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/        
params = {
                    "learning_rate"    :[0.2, 0.3,0.4,0.5],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[2, 3,4,5,6],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400,500],
                    "min_child_weight" :[1],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[2,3,4,5]
        }

In [14]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

7200
0
[0.2, 2, 100, 1, 0, 0.5, 1, 2]
accuracy     0.725
specificity  0.7437782805429864
sensitivity  0.49
auc          0.6168891402714932
1
----------------------------------------------------------------
[0.2, 2, 100, 1, 0, 0.5, 1, 3]
accuracy     0.6678571428571429
specificity  0.6783182503770739
sensitivity  0.54
auc          0.6091591251885369
----------------------------------------------------------------
2
----------------------------------------------------------------
[0.2, 2, 100, 1, 0, 0.5, 1, 4]
accuracy     0.6303571428571428
specificity  0.6340120663650075
sensitivity  0.59
auc          0.6120060331825038
----------------------------------------------------------------
3
----------------------------------------------------------------
[0.2, 2, 100, 1, 0, 0.5, 1, 5]
accuracy     0.6125
specificity  0.6167420814479638
sensitivity  0.565
auc          0.5908710407239819
----------------------------------------------------------------
4
[0.2, 2, 100, 1, 0, 0.5, 1.5, 2]
accura

----------------------------------------------------------------
[0.2, 2, 100, 1, 0, 1.0, 1.5, 5]
accuracy     0.6160714285714286
specificity  0.6147812971342383
sensitivity  0.64
auc          0.6273906485671191
----------------------------------------------------------------
32
[0.2, 2, 100, 1, 0, 1.0, 2, 2]
accuracy     0.7178571428571429
specificity  0.7418929110105581
sensitivity  0.42
auc          0.580946455505279
33
----------------------------------------------------------------
[0.2, 2, 100, 1, 0, 1.0, 2, 3]
accuracy     0.6571428571428571
specificity  0.6628959276018099
sensitivity  0.59
auc          0.626447963800905
----------------------------------------------------------------
34
----------------------------------------------------------------
[0.2, 2, 100, 1, 0, 1.0, 2, 4]
accuracy     0.6232142857142857
specificity  0.6263197586726998
sensitivity  0.59
auc          0.6081598793363499
----------------------------------------------------------------
35
[0.2, 2, 100, 1, 0

----------------------------------------------------------------
[0.2, 2, 100, 1, 0.5, 1.0, 1, 4]
accuracy     0.6392857142857142
specificity  0.6417043740573152
sensitivity  0.615
auc          0.6283521870286576
----------------------------------------------------------------
63
----------------------------------------------------------------
[0.2, 2, 100, 1, 0.5, 1.0, 1, 5]
accuracy     0.6214285714285714
specificity  0.622473604826546
sensitivity  0.615
auc          0.618736802413273
----------------------------------------------------------------
64
[0.2, 2, 100, 1, 0.5, 1.0, 1.5, 2]
accuracy     0.7089285714285715
specificity  0.7302413273001508
sensitivity  0.44
auc          0.5851206636500754
65
----------------------------------------------------------------
[0.2, 2, 100, 1, 0.5, 1.0, 1.5, 3]
accuracy     0.6660714285714285
specificity  0.6725113122171946
sensitivity  0.59
auc          0.6312556561085972
----------------------------------------------------------------
66
------

----------------------------------------------------------------
[0.2, 2, 200, 1, 0, 0.75, 2, 4]
accuracy     0.6982142857142857
specificity  0.7052790346907994
sensitivity  0.615
auc          0.6601395173453997
----------------------------------------------------------------
95
----------------------------------------------------------------
[0.2, 2, 200, 1, 0, 0.75, 2, 5]
accuracy     0.6732142857142857
specificity  0.6802790346907994
sensitivity  0.59
auc          0.6351395173453998
----------------------------------------------------------------
96
[0.2, 2, 200, 1, 0, 1.0, 1, 2]
accuracy     0.7482142857142857
specificity  0.7726244343891403
sensitivity  0.44
auc          0.6063122171945702
97
[0.2, 2, 200, 1, 0, 1.0, 1, 3]
accuracy     0.7196428571428571
specificity  0.7399321266968326
sensitivity  0.465
auc          0.6024660633484162
98
[0.2, 2, 200, 1, 0, 1.0, 1, 4]
accuracy     0.7125
specificity  0.7303544494720966
sensitivity  0.49
auc          0.6101772247360483
99
--------

----------------------------------------------------------------
[0.2, 2, 200, 1, 0.5, 0.75, 1.5, 4]
accuracy     0.6607142857142857
specificity  0.6667043740573152
sensitivity  0.59
auc          0.6283521870286576
----------------------------------------------------------------
127
----------------------------------------------------------------
[0.2, 2, 200, 1, 0.5, 0.75, 1.5, 5]
accuracy     0.6428571428571429
specificity  0.6436274509803921
sensitivity  0.64
auc          0.6418137254901961
----------------------------------------------------------------
128
[0.2, 2, 200, 1, 0.5, 0.75, 2, 2]
accuracy     0.7214285714285714
specificity  0.7399321266968326
sensitivity  0.49
auc          0.6149660633484163
129
----------------------------------------------------------------
[0.2, 2, 200, 1, 0.5, 0.75, 2, 3]
accuracy     0.6714285714285715
specificity  0.6840874811463047
sensitivity  0.515
auc          0.5995437405731523
----------------------------------------------------------------
1

...

[0.5, 6, 200, 1, 0.5, 1.0, 1.5, 5]
accuracy     0.6660714285714285
specificity  0.682315233785822
sensitivity  0.465
auc          0.573657616892911
6980
[0.5, 6, 200, 1, 0.5, 1.0, 2, 2]
accuracy     0.7571428571428571
specificity  0.7940045248868778
sensitivity  0.29
auc          0.542002262443439
6981
[0.5, 6, 200, 1, 0.5, 1.0, 2, 3]
accuracy     0.6892857142857143
specificity  0.7150452488687783
sensitivity  0.365
auc          0.5400226244343891
6982
[0.5, 6, 200, 1, 0.5, 1.0, 2, 4]
accuracy     0.6767857142857143
specificity  0.6957767722473605
sensitivity  0.44
auc          0.5678883861236802
6983
[0.5, 6, 200, 1, 0.5, 1.0, 2, 5]
accuracy     0.6571428571428571
specificity  0.6706259426847663
sensitivity  0.49
auc          0.5803129713423831
6984
[0.5, 6, 300, 1, 0, 0.5, 1, 2]
accuracy     0.7571428571428571
specificity  0.7958521870286577
sensitivity  0.265
auc          0.5304260935143288
6985
[0.5, 6, 300, 1, 0, 0.5, 1, 3]
accuracy     0.7285714285714285
specificity  0.7592006033

[0.5, 6, 300, 1, 0.5, 0.75, 1, 4]
accuracy     0.6982142857142857
specificity  0.7188536953242836
sensitivity  0.44
auc          0.5794268476621418
7035
[0.5, 6, 300, 1, 0.5, 0.75, 1, 5]
accuracy     0.7
specificity  0.7169306184012066
sensitivity  0.49
auc          0.6034653092006033
7036
[0.5, 6, 300, 1, 0.5, 0.75, 1.5, 2]
accuracy     0.7410714285714286
specificity  0.7727752639517346
sensitivity  0.34
auc          0.5563876319758673
7037
[0.5, 6, 300, 1, 0.5, 0.75, 1.5, 3]
accuracy     0.7089285714285715
specificity  0.732315233785822
sensitivity  0.415
auc          0.5736576168929111
7038
[0.5, 6, 300, 1, 0.5, 0.75, 1.5, 4]
accuracy     0.6946428571428571
specificity  0.7150452488687783
sensitivity  0.44
auc          0.5775226244343892
7039
[0.5, 6, 300, 1, 0.5, 0.75, 1.5, 5]
accuracy     0.6732142857142858
specificity  0.6957013574660633
sensitivity  0.39
auc          0.5428506787330317
7040
[0.5, 6, 300, 1, 0.5, 0.75, 2, 2]
accuracy     0.7357142857142858
specificity  0.76500754

[0.5, 6, 400, 1, 0, 1.0, 2, 3]
accuracy     0.7285714285714285
specificity  0.7611236802413273
sensitivity  0.315
auc          0.5380618401206636
7090
[0.5, 6, 400, 1, 0, 1.0, 2, 4]
accuracy     0.7107142857142857
specificity  0.7418929110105581
sensitivity  0.315
auc          0.528446455505279
7091
[0.5, 6, 400, 1, 0, 1.0, 2, 5]
accuracy     0.7053571428571428
specificity  0.7284313725490196
sensitivity  0.415
auc          0.5717156862745097
7092
[0.5, 6, 400, 1, 0.5, 0.5, 1, 2]
accuracy     0.7517857142857143
specificity  0.7881975867269985
sensitivity  0.29
auc          0.5390987933634992
7093
[0.5, 6, 400, 1, 0.5, 0.5, 1, 3]
accuracy     0.725
specificity  0.7515460030165912
sensitivity  0.39
auc          0.5707730015082956
7094
[0.5, 6, 400, 1, 0.5, 0.5, 1, 4]
accuracy     0.7017857142857142
specificity  0.7265082956259427
sensitivity  0.39
auc          0.5582541478129713
7095
[0.5, 6, 400, 1, 0.5, 0.5, 1, 5]
accuracy     0.7035714285714285
specificity  0.7246229260935143
sensitiv

[0.5, 6, 500, 1, 0, 0.75, 1.5, 2]
accuracy     0.7428571428571429
specificity  0.7804298642533937
sensitivity  0.265
auc          0.5227149321266968
7145
[0.5, 6, 500, 1, 0, 0.75, 1.5, 3]
accuracy     0.7214285714285714
specificity  0.7514705882352941
sensitivity  0.34
auc          0.5457352941176471
7146
[0.5, 6, 500, 1, 0, 0.75, 1.5, 4]
accuracy     0.7178571428571429
specificity  0.7400452488687783
sensitivity  0.44
auc          0.5900226244343891
7147
[0.5, 6, 500, 1, 0, 0.75, 1.5, 5]
accuracy     0.7089285714285715
specificity  0.7361236802413273
sensitivity  0.365
auc          0.5505618401206637
7148
[0.5, 6, 500, 1, 0, 0.75, 2, 2]
accuracy     0.7375
specificity  0.7765082956259427
sensitivity  0.24
auc          0.5082541478129714
7149
[0.5, 6, 500, 1, 0, 0.75, 2, 3]
accuracy     0.7357142857142858
specificity  0.7669306184012066
sensitivity  0.34
auc          0.5534653092006033
7150
[0.5, 6, 500, 1, 0, 0.75, 2, 4]
accuracy     0.7125
specificity  0.7400452488687783
sensitivity 

[0.5, 6, 500, 1, 0.5, 1.0, 2, 5]
accuracy     0.6571428571428571
specificity  0.6706259426847663
sensitivity  0.49
auc          0.5803129713423831


In [15]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.2, 2, 200, 1, 0, 0.75, 2, 4]
0.6982142857142857
0.7052790346907994
0.615
0.6601395173453997


In [17]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.65:
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.2, 2, 200, 1, 0, 0.75, 2, 4]
accuracy : 0.6982142857142857
spes     : 0.7052790346907994
sens     : 0.615
auc      : 0.6601395173453997
------------------------------------------------
parameters : [0.3, 2, 100, 1, 0, 1.0, 1.5, 4]
accuracy : 0.6857142857142857
spes     : 0.6918174962292609
sens     : 0.615
auc      : 0.6534087481146305
------------------------------------------------
parameters : [0.3, 2, 100, 1, 0.5, 1.0, 1.5, 4]
accuracy : 0.6535714285714286
spes     : 0.6532428355957768
sens     : 0.665
auc      : 0.6591214177978884
------------------------------------------------
parameters : [0.3, 2, 200, 1, 0.5, 1.0, 1.5, 4]
accuracy : 0.6535714285714286
spes     : 0.6532428355957768
sens     : 0.665
auc      : 0.6591214177978884
------------------------------------------------
parameters : [0.3, 2, 300, 1, 0.5, 1.0, 1.5, 4]
accuracy : 0.6535714285714286
spes     : 0.6532428355957768
sens     : 0.665
auc      : 0.6591214177978884
----------------------------------

## Καλύτερες τιμές για Ratio = 2 με min_child_weight=1:

    parameters : [0.2, 2, 200, 1, 0, 0.75, 2, 4]
    accuracy : 0.6982142857142857
    spes     : 0.7052790346907994
    sens     : 0.615
    auc      : 0.6601395173453997
    

# Ratio = 1

Αποτέλεσμα της gridsearch με τις ακόλουθες παραμέτρους, γίνονται print όλα και αυτά που ικανοποιούν την συνθήκη : if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5 είναι με bold και μεταξύ γραμμών.

In [15]:
params = {
                    "learning_rate"    :[0.1,0.2, 0.3,0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                    "min_child_weight" :[1],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3,4,5]
        }

In [16]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

8640
0
[0.1, 1, 100, 1, 0, 0.5, 1, 1]
accuracy     0.5178571428571429
specificity  0.5105580693815988
sensitivity  0.61
auc          0.5602790346907994
1
[0.1, 1, 100, 1, 0, 0.5, 1, 2]
accuracy     0.26071428571428573
specificity  0.210105580693816
sensitivity  0.905
auc          0.557552790346908
2
[0.1, 1, 100, 1, 0, 0.5, 1, 3]
accuracy     0.19107142857142856
specificity  0.13499245852187028
sensitivity  0.905
auc          0.5199962292609351
3
[0.1, 1, 100, 1, 0, 0.5, 1, 4]
accuracy     0.16785714285714287
specificity  0.10603318250377075
sensitivity  0.955
auc          0.5305165912518854
4
[0.1, 1, 100, 1, 0, 0.5, 1, 5]
accuracy     0.14285714285714285
specificity  0.07907239819004525
sensitivity  0.955
auc          0.5170361990950226
5
[0.1, 1, 100, 1, 0, 0.5, 1.5, 1]
accuracy     0.5125
specificity  0.5067496229260935
sensitivity  0.585
auc          0.5458748114630467
6
[0.1, 1, 100, 1, 0, 0.5, 1.5, 2]
accuracy     0.24285714285714285
specificity  0.19087481146304677
sensitivity 

[0.1, 1, 100, 1, 0.5, 0.5, 2, 1]
accuracy     0.5071428571428571
specificity  0.5009426847662142
sensitivity  0.585
auc          0.5429713423831071
56
[0.1, 1, 100, 1, 0.5, 0.5, 2, 2]
accuracy     0.2357142857142857
specificity  0.1831447963800905
sensitivity  0.905
auc          0.5440723981900453
57
[0.1, 1, 100, 1, 0.5, 0.5, 2, 3]
accuracy     0.16607142857142856
specificity  0.10414781297134239
sensitivity  0.955
auc          0.5295739064856712
58
[0.1, 1, 100, 1, 0.5, 0.5, 2, 4]
accuracy     0.13035714285714287
specificity  0.06557315233785822
sensitivity  0.955
auc          0.5102865761689291
59
[0.1, 1, 100, 1, 0.5, 0.5, 2, 5]
accuracy     0.12321428571428572
specificity  0.05788084464555053
sensitivity  0.955
auc          0.5064404223227753
60
[0.1, 1, 100, 1, 0.5, 0.75, 1, 1]
accuracy     0.5142857142857143
specificity  0.5067119155354449
sensitivity  0.61
auc          0.5583559577677225
61
[0.1, 1, 100, 1, 0.5, 0.75, 1, 2]
accuracy     0.2571428571428571
specificity  0.2062594

[0.1, 1, 100, 1, 1, 0.75, 1.5, 1]
accuracy     0.5017857142857143
specificity  0.49321266968325794
sensitivity  0.61
auc          0.5516063348416289
111
[0.1, 1, 100, 1, 1, 0.75, 1.5, 2]
accuracy     0.24107142857142858
specificity  0.18895173453996983
sensitivity  0.905
auc          0.5469758672699849
112
[0.1, 1, 100, 1, 1, 0.75, 1.5, 3]
accuracy     0.18392857142857144
specificity  0.1253393665158371
sensitivity  0.93
auc          0.5276696832579185
113
[0.1, 1, 100, 1, 1, 0.75, 1.5, 4]
accuracy     0.14464285714285716
specificity  0.08099547511312218
sensitivity  0.955
auc          0.5179977375565611
114
[0.1, 1, 100, 1, 1, 0.75, 1.5, 5]
accuracy     0.13392857142857142
specificity  0.06941930618401207
sensitivity  0.955
auc          0.5122096530920061
115
[0.1, 1, 100, 1, 1, 0.75, 2, 1]
accuracy     0.5107142857142857
specificity  0.5029034690799397
sensitivity  0.61
auc          0.5564517345399699
116
[0.1, 1, 100, 1, 1, 0.75, 2, 2]
accuracy     0.2357142857142857
specificity  0.

[0.1, 1, 200, 1, 0, 1.0, 1, 1]
accuracy     0.525
specificity  0.5164781297134239
sensitivity  0.635
auc          0.5757390648567119
166
[0.1, 1, 200, 1, 0, 1.0, 1, 2]
accuracy     0.3125
specificity  0.2736802413273002
sensitivity  0.805
auc          0.5393401206636501
167
[0.1, 1, 200, 1, 0, 1.0, 1, 3]
accuracy     0.2517857142857143
specificity  0.20049019607843138
sensitivity  0.905
auc          0.5527450980392157
168
[0.1, 1, 200, 1, 0, 1.0, 1, 4]
accuracy     0.23214285714285715
specificity  0.17737556561085974
sensitivity  0.93
auc          0.5536877828054299
169
[0.1, 1, 200, 1, 0, 1.0, 1, 5]
accuracy     0.20892857142857144
specificity  0.15230015082956258
sensitivity  0.93
auc          0.5411500754147813
170
[0.1, 1, 200, 1, 0, 1.0, 1.5, 1]
accuracy     0.5071428571428571
specificity  0.4971719457013575
sensitivity  0.635
auc          0.5660859728506787
171
[0.1, 1, 200, 1, 0, 1.0, 1.5, 2]
accuracy     0.30714285714285716
specificity  0.2659502262443439
sensitivity  0.83
auc 

[0.1, 1, 200, 1, 0.5, 1.0, 2, 1]
accuracy     0.5142857142857142
specificity  0.5067873303167421
sensitivity  0.61
auc          0.558393665158371
221
[0.1, 1, 200, 1, 0.5, 1.0, 2, 2]
accuracy     0.29464285714285715
specificity  0.25441176470588234
sensitivity  0.805
auc          0.5297058823529411
222
[0.1, 1, 200, 1, 0.5, 1.0, 2, 3]
accuracy     0.2375
specificity  0.18310708898944195
sensitivity  0.93
auc          0.5565535444947209
223
[0.1, 1, 200, 1, 0.5, 1.0, 2, 4]
accuracy     0.2
specificity  0.14272247360482654
sensitivity  0.93
auc          0.5363612368024132
224
[0.1, 1, 200, 1, 0.5, 1.0, 2, 5]
accuracy     0.16428571428571428
specificity  0.10411010558069382
sensitivity  0.93
auc          0.5170550527903469
225
[0.1, 1, 200, 1, 1, 0.5, 1, 1]
accuracy     0.5071428571428571
specificity  0.5009426847662142
sensitivity  0.585
auc          0.5429713423831071
226
[0.1, 1, 200, 1, 1, 0.5, 1, 2]
accuracy     0.2910714285714286
specificity  0.24283559577677225
sensitivity  0.905
a

...

[0.4, 4, 300, 1, 0, 0.75, 1, 1]
accuracy     0.5017857142857143
specificity  0.4915158371040724
sensitivity  0.64
auc          0.5657579185520362
8386
[0.4, 4, 300, 1, 0, 0.75, 1, 2]
accuracy     0.46964285714285714
specificity  0.45301659125188537
sensitivity  0.685
auc          0.5690082956259427
8387
[0.4, 4, 300, 1, 0, 0.75, 1, 3]
accuracy     0.4375
specificity  0.4144419306184012
sensitivity  0.735
auc          0.5747209653092006
8388
[0.4, 4, 300, 1, 0, 0.75, 1, 4]
accuracy     0.4267857142857143
specificity  0.40090497737556563
sensitivity  0.76
auc          0.5804524886877828
8389
[0.4, 4, 300, 1, 0, 0.75, 1, 5]
accuracy     0.41964285714285715
specificity  0.38759426847662143
sensitivity  0.835
auc          0.6112971342383107
8390
[0.4, 4, 300, 1, 0, 0.75, 1.5, 1]
accuracy     0.525
specificity  0.5127450980392156
sensitivity  0.685
auc          0.5988725490196078
8391
[0.4, 4, 300, 1, 0, 0.75, 1.5, 2]
accuracy     0.46964285714285714
specificity  0.45294117647058824
sensitiv

[0.4, 4, 300, 1, 0.5, 0.75, 2, 1]
accuracy     0.5446428571428571
specificity  0.5358974358974359
sensitivity  0.66
auc          0.597948717948718
8441
[0.4, 4, 300, 1, 0.5, 0.75, 2, 2]
accuracy     0.45357142857142857
specificity  0.4316742081447964
sensitivity  0.735
auc          0.5833371040723981
8442
[0.4, 4, 300, 1, 0.5, 0.75, 2, 3]
accuracy     0.4
specificity  0.3700603318250377
sensitivity  0.785
auc          0.5775301659125188
8443
[0.4, 4, 300, 1, 0.5, 0.75, 2, 4]
accuracy     0.375
specificity  0.34306184012066365
sensitivity  0.785
auc          0.5640309200603318
8444
[0.4, 4, 300, 1, 0.5, 0.75, 2, 5]
accuracy     0.36607142857142855
specificity  0.3295625942684766
sensitivity  0.835
auc          0.5822812971342383
8445
[0.4, 4, 300, 1, 0.5, 1.0, 1, 1]
accuracy     0.5428571428571428
specificity  0.5376696832579185
sensitivity  0.61
auc          0.5738348416289593
8446
[0.4, 4, 300, 1, 0.5, 1.0, 1, 2]
accuracy     0.45714285714285713
specificity  0.43171191553544497
sensit

[0.4, 4, 300, 1, 1, 1.0, 1.5, 1]
accuracy     0.5375
specificity  0.5338612368024133
sensitivity  0.585
auc          0.5594306184012067
8496
[0.4, 4, 300, 1, 1, 1.0, 1.5, 2]
accuracy     0.4017857142857143
specificity  0.3738310708898944
sensitivity  0.76
auc          0.5669155354449472
8497
[0.4, 4, 300, 1, 1, 1.0, 1.5, 3]
accuracy     0.3660714285714286
specificity  0.3333333333333333
sensitivity  0.785
auc          0.5591666666666667
8498
[0.4, 4, 300, 1, 1, 1.0, 1.5, 4]
accuracy     0.3482142857142857
specificity  0.3102187028657617
sensitivity  0.835
auc          0.5726093514328808
8499
[0.4, 4, 300, 1, 1, 1.0, 1.5, 5]
accuracy     0.3392857142857143
specificity  0.29683257918552036
sensitivity  0.885
auc          0.5909162895927602
8500
[0.4, 4, 300, 1, 1, 1.0, 2, 1]
accuracy     0.5303571428571429
specificity  0.526131221719457
sensitivity  0.585
auc          0.5555656108597286
8501
[0.4, 4, 300, 1, 1, 1.0, 2, 2]
accuracy     0.3964285714285714
specificity  0.36617647058823527
s

[0.4, 4, 400, 1, 0.5, 0.5, 1, 1]
accuracy     0.5428571428571428
specificity  0.5378205128205128
sensitivity  0.61
auc          0.5739102564102564
8551
[0.4, 4, 400, 1, 0.5, 0.5, 1, 2]
accuracy     0.45535714285714285
specificity  0.4317873303167421
sensitivity  0.76
auc          0.595893665158371
8552
[0.4, 4, 400, 1, 0.5, 0.5, 1, 3]
accuracy     0.41428571428571426
specificity  0.3854826546003016
sensitivity  0.785
auc          0.5852413273001509
8553
[0.4, 4, 400, 1, 0.5, 0.5, 1, 4]
accuracy     0.40535714285714286
specificity  0.3739441930618401
sensitivity  0.81
auc          0.5919720965309201
8554
[0.4, 4, 400, 1, 0.5, 0.5, 1, 5]
accuracy     0.37857142857142856
specificity  0.34502262443438914
sensitivity  0.81
auc          0.5775113122171945
8555
[0.4, 4, 400, 1, 0.5, 0.5, 1.5, 1]
accuracy     0.5303571428571429
specificity  0.5243589743589744
sensitivity  0.61
auc          0.5671794871794872
8556
[0.4, 4, 400, 1, 0.5, 0.5, 1.5, 2]
accuracy     0.45535714285714285
specificity  

[0.4, 4, 400, 1, 1, 0.5, 2, 1]
accuracy     0.525
specificity  0.5242458521870287
sensitivity  0.54
auc          0.5321229260935143
8606
[0.4, 4, 400, 1, 1, 0.5, 2, 2]
accuracy     0.4107142857142857
specificity  0.3834841628959276
sensitivity  0.76
auc          0.5717420814479638
8607
[0.4, 4, 400, 1, 1, 0.5, 2, 3]
accuracy     0.37857142857142856
specificity  0.34498491704374057
sensitivity  0.81
auc          0.5774924585218703
8608
[0.4, 4, 400, 1, 1, 0.5, 2, 4]
accuracy     0.3517857142857143
specificity  0.316025641025641
sensitivity  0.81
auc          0.5630128205128205
8609
[0.4, 4, 400, 1, 1, 0.5, 2, 5]
accuracy     0.34285714285714286
specificity  0.3044494720965309
sensitivity  0.835
auc          0.5697247360482655
8610
[0.4, 4, 400, 1, 1, 0.75, 1, 1]
accuracy     0.5375
specificity  0.5301282051282051
sensitivity  0.635
auc          0.5825641025641025
8611
[0.4, 4, 400, 1, 1, 0.75, 1, 2]
accuracy     0.4446428571428572
specificity  0.4201734539969834
sensitivity  0.76
auc   

In [18]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.2, 3, 200, 1, 0, 0.5, 1, 1]
0.5482142857142858
0.5339366515837104
0.735
0.6344683257918552


In [21]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.62:
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.1, 2, 400, 1, 0, 0.5, 1, 1]
accuracy : 0.5428571428571428
spes     : 0.5301282051282051
sens     : 0.71
auc      : 0.6200641025641025
------------------------------------------------
parameters : [0.1, 4, 400, 1, 0, 0.5, 1, 1]
accuracy : 0.5375
spes     : 0.5223981900452489
sens     : 0.735
auc      : 0.6286990950226244
------------------------------------------------
parameters : [0.2, 2, 300, 1, 0, 0.75, 1, 1]
accuracy : 0.5267857142857143
spes     : 0.5108220211161387
sens     : 0.735
auc      : 0.6229110105580694
------------------------------------------------
parameters : [0.2, 3, 100, 1, 0, 0.5, 1, 1]
accuracy : 0.5482142857142858
spes     : 0.5358974358974359
sens     : 0.71
auc      : 0.622948717948718
------------------------------------------------
parameters : [0.2, 3, 200, 1, 0, 0.5, 1, 1]
accuracy : 0.5482142857142858
spes     : 0.5339366515837104
sens     : 0.735
auc      : 0.6344683257918552
------------------------------------------------
parameters : [

In [23]:
#Τυπώνονται περιπτώσεις που accuracy<0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][1] > 0.53 and best_params[i][2] > 0.53 and best_params[i][3] > 0.6 and best_params[i][4] > 0.62:
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.1, 2, 400, 1, 0, 0.5, 1, 1]
accuracy : 0.5428571428571428
spes     : 0.5301282051282051
sens     : 0.71
auc      : 0.6200641025641025
------------------------------------------------
parameters : [0.2, 3, 100, 1, 0, 0.5, 1, 1]
accuracy : 0.5482142857142858
spes     : 0.5358974358974359
sens     : 0.71
auc      : 0.622948717948718
------------------------------------------------
parameters : [0.2, 3, 200, 1, 0, 0.5, 1, 1]
accuracy : 0.5482142857142858
spes     : 0.5339366515837104
sens     : 0.735
auc      : 0.6344683257918552
------------------------------------------------
parameters : [0.3, 3, 100, 1, 0.5, 0.5, 2, 1]
accuracy : 0.5446428571428572
spes     : 0.5320135746606335
sens     : 0.71
auc      : 0.6210067873303168
------------------------------------------------
parameters : [0.3, 4, 300, 1, 0, 0.75, 1.5, 1]
accuracy : 0.5446428571428571
spes     : 0.5319758672699849
sens     : 0.71
auc      : 0.6209879336349925
------------------------------------------------


## Καλύτερες τιμές για Ratio = 1 με min_child_weight=1:

    parameters : [0.2, 3, 200, 1, 0, 0.5, 1, 1]
    accuracy : 0.5482142857142858
    spes     : 0.5339366515837104
    sens     : 0.735
    auc      : 0.6344683257918552

# Ratio = 3

Αποτέλεσμα της gridsearch με τις ακόλουθες παραμέτρους, γίνονται print όλα και αυτά που ικανοποιούν την συνθήκη : if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5 είναι με bold και μεταξύ γραμμών.

In [13]:
params = {
                    "learning_rate"    :[0.1,0.2, 0.3,0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                    "min_child_weight" :[1],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3,4]
        }

In [14]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

6912
0
[0.1, 1, 100, 1, 0, 0.5, 1, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
1
[0.1, 1, 100, 1, 0, 0.5, 1, 2]
accuracy     0.7714285714285715
specificity  0.8093891402714932
sensitivity  0.29
auc          0.5496945701357466
2
----------------------------------------------------------------
[0.1, 1, 100, 1, 0, 0.5, 1, 3]
accuracy     0.6392857142857142
specificity  0.6475490196078432
sensitivity  0.54
auc          0.5937745098039215
----------------------------------------------------------------
3
[0.1, 1, 100, 1, 0, 0.5, 1, 4]
accuracy     0.5071428571428571
specificity  0.493288084464555
sensitivity  0.685
auc          0.5891440422322776
4
[0.1, 1, 100, 1, 0, 0.5, 1.5, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
5
[0.1, 1, 100, 1, 0, 0.5, 1.5, 2]
accuracy     0.7875
specificity  0.8266968325791855
sensitivity  0.29
auc          0.5583484162895928
6
---------------------------------------

[0.1, 1, 100, 1, 0.5, 0.75, 1, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
49
[0.1, 1, 100, 1, 0.5, 0.75, 1, 2]
accuracy     0.775
specificity  0.815158371040724
sensitivity  0.265
auc          0.5400791855203619
50
----------------------------------------------------------------
[0.1, 1, 100, 1, 0.5, 0.75, 1, 3]
accuracy     0.6410714285714286
specificity  0.6495098039215687
sensitivity  0.54
auc          0.5947549019607843
----------------------------------------------------------------
51
[0.1, 1, 100, 1, 0.5, 0.75, 1, 4]
accuracy     0.5071428571428571
specificity  0.493288084464555
sensitivity  0.685
auc          0.5891440422322776
52
[0.1, 1, 100, 1, 0.5, 0.75, 1.5, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
53
[0.1, 1, 100, 1, 0.5, 0.75, 1.5, 2]
accuracy     0.7821428571428571
specificity  0.8228506787330316
sensitivity  0.265
auc          0.5439253393665158
54
----------------------

[0.1, 1, 100, 1, 1, 0.75, 2, 4]
accuracy     0.5053571428571428
specificity  0.4914404223227753
sensitivity  0.685
auc          0.5882202111613877
96
[0.1, 1, 100, 1, 1, 1.0, 1, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
97
[0.1, 1, 100, 1, 1, 1.0, 1, 2]
accuracy     0.775
specificity  0.8151960784313725
sensitivity  0.265
auc          0.5400980392156862
98
----------------------------------------------------------------
[0.1, 1, 100, 1, 1, 1.0, 1, 3]
accuracy     0.6410714285714285
specificity  0.6475867269984917
sensitivity  0.565
auc          0.6062933634992458
----------------------------------------------------------------
99
[0.1, 1, 100, 1, 1, 1.0, 1, 4]
accuracy     0.5053571428571428
specificity  0.4913650075414781
sensitivity  0.685
auc          0.5881825037707391
100
[0.1, 1, 100, 1, 1, 1.0, 1.5, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
101
[0.1, 1, 100, 1, 1, 1.0, 1.5, 2]
acc

[0.1, 1, 200, 1, 0, 1.0, 1.5, 4]
accuracy     0.575
specificity  0.5723604826546003
sensitivity  0.615
auc          0.5936802413273001
140
[0.1, 1, 200, 1, 0, 1.0, 2, 1]
accuracy     0.8803571428571428
specificity  0.9441930618401206
sensitivity  0.07
auc          0.5070965309200604
141
[0.1, 1, 200, 1, 0, 1.0, 2, 2]
accuracy     0.7589285714285714
specificity  0.7939668174962292
sensitivity  0.315
auc          0.5544834087481146
142
----------------------------------------------------------------
[0.1, 1, 200, 1, 0, 1.0, 2, 3]
accuracy     0.6607142857142857
specificity  0.6686651583710407
sensitivity  0.565
auc          0.6168325791855204
----------------------------------------------------------------
143
[0.1, 1, 200, 1, 0, 1.0, 2, 4]
accuracy     0.5696428571428571
specificity  0.5665912518853695
sensitivity  0.615
auc          0.5907956259426848
144
[0.1, 1, 200, 1, 0.5, 0.5, 1, 1]
accuracy     0.8767857142857143
specificity  0.936500754147813
sensitivity  0.12
auc          0.528

----------------------------------------------------------------
[0.1, 1, 200, 1, 1, 0.5, 1, 3]
accuracy     0.6625
specificity  0.6686651583710407
sensitivity  0.59
auc          0.6293325791855203
----------------------------------------------------------------
183
[0.1, 1, 200, 1, 1, 0.5, 1, 4]
accuracy     0.5696428571428571
specificity  0.5666289592760181
sensitivity  0.615
auc          0.590814479638009
184
[0.1, 1, 200, 1, 1, 0.5, 1.5, 1]
accuracy     0.9071428571428571
specificity  0.9730769230769231
sensitivity  0.07
auc          0.5215384615384615
185
[0.1, 1, 200, 1, 1, 0.5, 1.5, 2]
accuracy     0.7517857142857143
specificity  0.786236802413273
sensitivity  0.315
auc          0.5506184012066365
186
----------------------------------------------------------------
[0.1, 1, 200, 1, 1, 0.5, 1.5, 3]
accuracy     0.6607142857142857
specificity  0.6686651583710407
sensitivity  0.565
auc          0.6168325791855204
----------------------------------------------------------------
187


...

[0.4, 4, 200, 1, 0.5, 1.0, 1.5, 4]
accuracy     0.8035714285714286
specificity  0.8459276018099547
sensitivity  0.265
auc          0.5554638009049774
6656
[0.4, 4, 200, 1, 0.5, 1.0, 2, 1]
accuracy     0.8678571428571429
specificity  0.9307315233785822
sensitivity  0.07
auc          0.500365761689291
6657
[0.4, 4, 200, 1, 0.5, 1.0, 2, 2]
accuracy     0.8428571428571429
specificity  0.892156862745098
sensitivity  0.215
auc          0.553578431372549
6658
[0.4, 4, 200, 1, 0.5, 1.0, 2, 3]
accuracy     0.825
specificity  0.8691176470588236
sensitivity  0.265
auc          0.5670588235294117
6659
[0.4, 4, 200, 1, 0.5, 1.0, 2, 4]
accuracy     0.8035714285714286
specificity  0.8460030165912519
sensitivity  0.265
auc          0.555501508295626
6660
[0.4, 4, 200, 1, 1, 0.5, 1, 1]
accuracy     0.8696428571428572
specificity  0.9268476621417798
sensitivity  0.145
auc          0.5359238310708899
6661
[0.4, 4, 200, 1, 1, 0.5, 1, 2]
accuracy     0.8464285714285714
specificity  0.8921568627450981
sensi

[0.4, 4, 300, 1, 0, 0.75, 1, 3]
accuracy     0.8089285714285714
specificity  0.8593514328808447
sensitivity  0.165
auc          0.5121757164404224
6711
[0.4, 4, 300, 1, 0, 0.75, 1, 4]
accuracy     0.8142857142857143
specificity  0.8631975867269985
sensitivity  0.19
auc          0.5265987933634992
6712
[0.4, 4, 300, 1, 0, 0.75, 1.5, 1]
accuracy     0.8553571428571428
specificity  0.9114253393665158
sensitivity  0.145
auc          0.5282126696832579
6713
[0.4, 4, 300, 1, 0, 0.75, 1.5, 2]
accuracy     0.8285714285714285
specificity  0.8843891402714932
sensitivity  0.12
auc          0.5021945701357466
6714
[0.4, 4, 300, 1, 0, 0.75, 1.5, 3]
accuracy     0.8196428571428571
specificity  0.8709276018099548
sensitivity  0.17
auc          0.5204638009049773
6715
[0.4, 4, 300, 1, 0, 0.75, 1.5, 4]
accuracy     0.8107142857142857
specificity  0.8594268476621418
sensitivity  0.19
auc          0.5247134238310709
6716
[0.4, 4, 300, 1, 0, 0.75, 2, 1]
accuracy     0.8517857142857143
specificity  0.90761

[0.4, 4, 300, 1, 0.5, 1.0, 2, 2]
accuracy     0.8428571428571429
specificity  0.892156862745098
sensitivity  0.215
auc          0.553578431372549
6766
[0.4, 4, 300, 1, 0.5, 1.0, 2, 3]
accuracy     0.825
specificity  0.8691176470588236
sensitivity  0.265
auc          0.5670588235294117
6767
[0.4, 4, 300, 1, 0.5, 1.0, 2, 4]
accuracy     0.8035714285714286
specificity  0.8460030165912519
sensitivity  0.265
auc          0.555501508295626
6768
[0.4, 4, 300, 1, 1, 0.5, 1, 1]
accuracy     0.8696428571428572
specificity  0.9268476621417798
sensitivity  0.145
auc          0.5359238310708899
6769
[0.4, 4, 300, 1, 1, 0.5, 1, 2]
accuracy     0.8446428571428571
specificity  0.8902337858220212
sensitivity  0.265
auc          0.5776168929110106
6770
[0.4, 4, 300, 1, 1, 0.5, 1, 3]
accuracy     0.8142857142857143
specificity  0.8613499245852188
sensitivity  0.215
auc          0.5381749622926093
6771
[0.4, 4, 300, 1, 1, 0.5, 1, 4]
accuracy     0.8053571428571429
specificity  0.8440422322775264
sensitivi

[0.4, 4, 400, 1, 0, 0.75, 1.5, 1]
accuracy     0.8553571428571428
specificity  0.9114253393665158
sensitivity  0.145
auc          0.5282126696832579
6821
[0.4, 4, 400, 1, 0, 0.75, 1.5, 2]
accuracy     0.8232142857142857
specificity  0.8805052790346908
sensitivity  0.095
auc          0.48775263951734543
6822
[0.4, 4, 400, 1, 0, 0.75, 1.5, 3]
accuracy     0.8196428571428571
specificity  0.8728506787330317
sensitivity  0.145
auc          0.5089253393665158
6823
[0.4, 4, 400, 1, 0, 0.75, 1.5, 4]
accuracy     0.8142857142857143
specificity  0.8632730015082957
sensitivity  0.19
auc          0.5266365007541478
6824
[0.4, 4, 400, 1, 0, 0.75, 2, 1]
accuracy     0.85
specificity  0.9056561085972851
sensitivity  0.145
auc          0.5253280542986425
6825
[0.4, 4, 400, 1, 0, 0.75, 2, 2]
accuracy     0.8303571428571428
specificity  0.8863122171945701
sensitivity  0.12
auc          0.5031561085972851
6826
[0.4, 4, 400, 1, 0, 0.75, 2, 3]
accuracy     0.8214285714285714
specificity  0.8748114630467572

[0.4, 4, 400, 1, 0.5, 1.0, 2, 4]
accuracy     0.8035714285714286
specificity  0.8460030165912519
sensitivity  0.265
auc          0.555501508295626
6876
[0.4, 4, 400, 1, 1, 0.5, 1, 1]
accuracy     0.8678571428571429
specificity  0.9249245852187029
sensitivity  0.145
auc          0.5349622926093515
6877
[0.4, 4, 400, 1, 1, 0.5, 1, 2]
accuracy     0.8464285714285714
specificity  0.8921568627450981
sensitivity  0.265
auc          0.578578431372549
6878
[0.4, 4, 400, 1, 1, 0.5, 1, 3]
accuracy     0.8160714285714286
specificity  0.8633107088989442
sensitivity  0.215
auc          0.5391553544494722
6879
[0.4, 4, 400, 1, 1, 0.5, 1, 4]
accuracy     0.8089285714285714
specificity  0.8478883861236802
sensitivity  0.315
auc          0.5814441930618401
6880
[0.4, 4, 400, 1, 1, 0.5, 1.5, 1]
accuracy     0.8642857142857143
specificity  0.9249245852187029
sensitivity  0.095
auc          0.5099622926093514
6881
[0.4, 4, 400, 1, 1, 0.5, 1.5, 2]
accuracy     0.8446428571428571
specificity  0.894079939668

In [15]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.1, 2, 100, 1, 1, 1.0, 1.5, 4]
0.6821428571428572
0.6879336349924585
0.615
0.6514668174962293


In [17]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.64:
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.1, 2, 100, 1, 0, 1.0, 1, 4]
accuracy : 0.6839285714285714
spes     : 0.6917420814479638
sens     : 0.59
auc      : 0.6408710407239819
------------------------------------------------
parameters : [0.1, 2, 100, 1, 0.5, 0.5, 1.5, 4]
accuracy : 0.6678571428571428
spes     : 0.6725113122171946
sens     : 0.615
auc      : 0.6437556561085972
------------------------------------------------
parameters : [0.1, 2, 100, 1, 0.5, 1.0, 1.5, 4]
accuracy : 0.675
spes     : 0.6802036199095023
sens     : 0.615
auc      : 0.6476018099547511
------------------------------------------------
parameters : [0.1, 2, 100, 1, 1, 1.0, 1, 4]
accuracy : 0.6678571428571429
spes     : 0.6725113122171946
sens     : 0.615
auc      : 0.6437556561085973
------------------------------------------------
parameters : [0.1, 2, 100, 1, 1, 1.0, 1.5, 4]
accuracy : 0.6821428571428572
spes     : 0.6879336349924585
sens     : 0.615
auc      : 0.6514668174962293
------------------------------------------------
para

## Καλύτερες τιμές για Ratio = 3 με min_child_weight=1:

    parameters : [0.1, 2, 100, 1, 0, 1.0, 1, 4]
    accuracy : 0.6839285714285714
    spes     : 0.6917420814479638
    sens     : 0.59
    auc      : 0.6408710407239819

    parameters : [0.1, 2, 100, 1, 1, 1.0, 1.5, 4]
    accuracy : 0.6821428571428572
    spes     : 0.6879336349924585
    sens     : 0.615
    auc      : 0.6514668174962293